# Macroeconomic Analysis
Demonstration of macroeconomic analysis using Python, Jupyter Notebooks, external data, and API calls. Comparison between Aotearoa New Zealand and major trading partners (USA, China, Australia, Japan, Democratic Republic of Korea, Singapore, United Kingdom).
1. Gross Domestic Product ([NZ Stats](https://www.stats.govt.nz/large-datasets/csv-files-for-download/))
2. Consumer Price Index ([NZ Stats](https://www.stats.govt.nz/large-datasets/csv-files-for-download/))
3. Exchange Rates ([Federal Reserve Economic Data using FRED API](https://fred.stlouisfed.org))
4. Trade Balances ([NZ Stats](https://www.stats.govt.nz/large-datasets/csv-files-for-download/))
5. Equity Markets ([Yahoo Finance](https://nz.finance.yahoo.com))
6. Commodities Proxies ([Yahoo Finance](https://nz.finance.yahoo.com))

In [129]:
# Import Python Modules
import os
import dotenv as dv
import pandas as pd
import numpy as np
import scipy as sp
import matplotlib.pyplot as plt
import plotly as ply
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import seaborn as sns
import sklearn as skl
import yfinance as yf
import requests

## Gross Domestic Product (GDP)
Preprocess and visualise gross domestic product from NZ Stats denoted by the following series:
### Key Aggregates
- **Real GDP (Chain Volume):** 'Series, Key aggregates, Chain volume, Actual, Total'
- **Nominal GDP (Nominal):** 'Series, Key aggregates, Nominal, Actual, Total'
### Production Approach (GDP(P))
- Real GDP - Total value of Goods Produced (Chain Volume): 'Series, GDP(P), Chain volume, Actual, Total'
### Expenditure Approach (GDP(E))
- Real GDP - Total value of Expenditure (Chain Volume): 'Series, GDP(E), Chain volume, Actual, Total'
- Nominal GDP - Total value of expenditure (Nominal): 'GDP(E), Nominal, Actual, Total'
### Income Approach (GDP(I))
- GDP(I) adjusted for Inflation - Income generated by production (Nominal): 'GDP(I), current prices'

In [94]:
# Inspect GDP dataframe
gdp_fp = '../../data/raw/nz_stats/economy/gross-domestic-product-march-2025-quarter.csv'
gdp_df = pd.read_csv(gdp_fp)

In [95]:
# Key Groupings
gdp_key_agg_real = 'Series, Key aggregates, Chain volume, Actual, Total'
gdp_key_agg_nominal = 'Series, Key aggregates, Nominal, Actual, Total'
gdp_p_nominal = 'GDP(P), Nominal, Actual, Total'
gdp_p_real = 'Series, GDP(P), Chain volume, Actual, Total'
gdp_e_nominal = 'Series, GDP(E), Nominal, Actual, Total'
gdp_e_real = 'Series, GDP(E), Chain volume, Actual, Total'
gdp_i_nominal = 'Series, GDP(I), current prices'
key_groupings = [gdp_key_agg_real, gdp_key_agg_nominal, gdp_p_nominal, gdp_p_real, gdp_e_nominal, gdp_e_real, gdp_i_nominal]

# Determine string columns
str_cols = gdp_df.select_dtypes(include=['object']).columns
num_cols = gdp_df.select_dtypes(include=['float64', 'int64']).columns

# Display unique values in the string columns.
for col in str_cols:
    print(f"Unique values in {col}: {gdp_df[col].nunique()}")
    print(gdp_df[col].unique())

# Process GDP Dataframe; write to processed data folder.
def process_gdp(df: pd.DataFrame) -> pd.DataFrame:
    """
    Process GDP dataframe for analysis.
    Involves removing redundant columns, nan values, transforming data.
    :param raw df:
    :return: processed DataFrame
    """
    # Drop unnecessary columns
    df = df.drop(columns=['Series_title_4','Series_title_5'])
    # Filter for the key groupings
    df = df[df['Group'].isin(key_groupings)]
    # Rename columns for clarity
    df = df.rename(columns={'Period': 'period', 'Data_value': 'value', 'STATUS': 'status'})
    # Convert period to timestamp e.g., 1980.03 to datetime
    df['year'] = df['period'].astype(str).str.split('.').str[0].astype(int)
    df['month'] = df['period'].astype(str).str.split('.').str[1].astype(int)
    date_df = df[['year', 'month']]
    df['date'] = pd.to_datetime(date_df.assign(day=1))
    return df

# Use processing function.
gdp_processed_df = process_gdp(gdp_df)
str_cols = gdp_processed_df.select_dtypes(include=['object']).columns
num_cols = gdp_processed_df.select_dtypes(include=['float64', 'int64']).columns

# Display unique values in the string columns.
for col in str_cols:
    print(f"Unique values in {col}: {gdp_processed_df[col].nunique()}")
    print(gdp_processed_df[col].unique())

# Save processed GDP data for reuse.
gdp_processed_df.to_csv('../../data/processed/nz_stats/gdp.csv')

Unique values in Series_reference: 1004
['SNEA.SG00NAC00B15' 'SNEA.SG00NAC00B15D' 'SNEA.SG00NAC00B15J' ...
 'SNEQ.SG09RSC00B01NZ' 'SNEQ.SG09RSC00B06NZ' 'SNEQ.SG09RSC00B15NZ']
Unique values in STATUS: 3
['FINAL' 'REVISED' 'CONFIDENTIAL']
Unique values in UNITS: 3
['Dollars' 'Index' 'Percent']
Unique values in Subject: 1
['National Accounts - SNA 2008 - SNE']
Unique values in Group: 82
['Series, Key aggregates, Nominal, Actual, Total'
 'Series, Rolling Annuals, Key aggregates, Nominal, Actual, Total'
 'Series, Key aggregates, Chain volume, Actual, Total'
 'Series, Rolling Annuals, Key aggregates, Chain volume, Actual, Total'
 'Series, GDP(P), Chain volume, Actual, Total'
 'Series, GDP(P), Chain volume, Actual, HOTP industry groups'
 'Series, Rolling Annuals, Chain volume, Actual, HOTP industry'
 'Series, GDP(P), Chain volume, Actual, ANZSIC06 high-level industry groups'
 'Series, GDP(P), Chain volume, Actual, ANZSIC06 industry groups'
 'Series, GDP(E), Nominal, Actual, Total'
 'Series, G

In [131]:
# Model the GDP Data in a series of charts.
gdp_processed_df.info()
# Nominal GDP (Nominal): 'Series, Key aggregates, Nominal, Actual, Total'
gdp_nom_df = gdp_processed_df[gdp_processed_df['Group'].isin(['Series, Key aggregates, Nominal, Actual, Total'])]
gdp_nom_df = gdp_nom_df[gdp_nom_df['Series_title_1'] == 'Gross Domestic Product - expenditure measure']
max_ind = min(max(gdp_nom_df.index),100) # Trick to separate maximum and minimum data.
gdp_nom_annual_df = gdp_nom_df.loc[:max_ind].copy()
gdp_nom_annual_df['pct_change'] = gdp_nom_annual_df['value'].pct_change() * 100
gdp_nom_annual_df.to_csv('../../data/processed/nz_stats/gdp_nom_annual.csv')

# Quarterly Calculations
gdp_nom_quarterly_df = gdp_nom_df.loc[max_ind+1:].copy()
gdp_nom_quarterly_df['pct_change'] = gdp_nom_quarterly_df['value'].pct_change() * 100
gdp_nom_quarterly_df.to_csv('../../data/processed/nz_stats/gdp_nom_quarterly.csv')

# Real GDP (Chain Volume): 'Series, Key aggregates, Chain volume, Actual, Total'
gdp_real_df = gdp_processed_df[gdp_processed_df['Group'].isin(['Series, Key aggregates, Chain volume, Actual, Total'])]
gdp_real_df = gdp_real_df[gdp_real_df['Series_title_1'] == 'Gross Domestic Product - expenditure measure']
max_ind = min(max(gdp_real_df.index),1000) # Trick to separate maximum and minimum data.
gdp_real_annual_df = gdp_real_df.loc[:max_ind].copy()
gdp_real_annual_df['pct_change'] = gdp_real_annual_df['value'].pct_change() * 100
gdp_real_annual_df.to_csv('../../data/processed/nz_stats/gdp_real_annual.csv')

# Quarterly Calculations
gdp_real_quarterly_df = gdp_real_df.loc[max_ind+1:].copy()
gdp_real_quarterly_df['pct_change'] = gdp_real_quarterly_df['value'].pct_change() * 100
gdp_real_quarterly_df.to_csv('../../data/processed/nz_stats/gdp_real_quarterly.csv')

# Create a subplot with secondary y-axis
fig = make_subplots(specs=[[{"secondary_y": True}]])

# Left y-axis: GDP levels
fig.add_trace(
    go.Scatter(
        x=gdp_nom_annual_df["date"],
        y=gdp_nom_annual_df["value"],
        name="Nominal GDP",
        mode="lines",
        line=dict(color="blue")
    ),
    secondary_y=False
)

fig.add_trace(
    go.Scatter(
        x=gdp_real_annual_df["date"],
        y=gdp_real_annual_df["value"],
        name="Real GDP",
        mode="lines",
        line=dict(color="orange")
    ),
    secondary_y=False
)

# Right y-axis: % changes
fig.add_trace(
    go.Scatter(
        x=gdp_nom_annual_df["date"],
        y=gdp_nom_annual_df["pct_change"],
        name="Nominal GDP % Change",
        mode="lines",
        line=dict(color="green", dash="dash")
    ),
    secondary_y=True
)

fig.add_trace(
    go.Scatter(
        x=gdp_real_annual_df["date"],
        y=gdp_real_annual_df["pct_change"],
        name="Real GDP % Change",
        mode="lines",
        line=dict(color="red", dash="dash")
    ),
    secondary_y=True
)

# Layout settings
fig.update_layout(
    title_text="New Zealand Nominal vs Real GDP (Annual)",
    height=600,
    width=1100,
    hovermode="x unified",
    legend=dict(orientation="h", yanchor="bottom", y=1.02, xanchor="left", x=0)
)

# Axis labels
fig.update_xaxes(title_text="Year", showgrid=True)
fig.update_yaxes(title_text="GDP (in millions)", secondary_y=False, showgrid=True)
fig.update_yaxes(title_text="Percentage Change (%)", secondary_y=True)

fig.show()

# One figure with a secondary y-axis
fig = make_subplots(specs=[[{"secondary_y": True}]])

# Left y-axis: GDP levels
fig.add_trace(
    go.Scatter(
        x=gdp_nom_quarterly_df["date"],
        y=gdp_nom_quarterly_df["value"],
        name="Nominal GDP",
        mode="lines"
    ),
    secondary_y=False
)
fig.add_trace(
    go.Scatter(
        x=gdp_real_quarterly_df["date"],
        y=gdp_real_quarterly_df["value"],
        name="Real GDP",
        mode="lines"
    ),
    secondary_y=False
)

# Right y-axis: % changes
fig.add_trace(
    go.Scatter(
        x=gdp_nom_quarterly_df["date"],
        y=gdp_nom_quarterly_df["pct_change"],
        name="Nominal GDP % Change",
        mode="lines",
        line=dict(dash="dash")
    ),
    secondary_y=True
)
fig.add_trace(
    go.Scatter(
        x=gdp_real_quarterly_df["date"],
        y=gdp_real_quarterly_df["pct_change"],
        name="Real GDP % Change",
        mode="lines",
        line=dict(dash="dash")
    ),
    secondary_y=True
)

# Labels, title, layout
fig.update_layout(
    title_text="New Zealand Nominal vs Real GDP (Quarterly)",
    height=600,
    width=1100,
    hovermode="x unified",
    legend=dict(orientation="h", yanchor="bottom", y=1.02, xanchor="left", x=0)
)

fig.update_xaxes(title_text="Year", showgrid=True)
fig.update_yaxes(title_text="GDP (in millions)", secondary_y=False, showgrid=True)
fig.update_yaxes(title_text="Percentage Change (%)", secondary_y=True)

fig.show()


<class 'pandas.core.frame.DataFrame'>
Index: 3248 entries, 0 to 62072
Data columns (total 14 columns):
 #   Column            Non-Null Count  Dtype         
---  ------            --------------  -----         
 0   Series_reference  3248 non-null   object        
 1   period            3248 non-null   float64       
 2   value             3248 non-null   float64       
 3   status            3248 non-null   object        
 4   UNITS             3248 non-null   object        
 5   MAGNITUDE         3248 non-null   int64         
 6   Subject           3248 non-null   object        
 7   Group             3248 non-null   object        
 8   Series_title_1    3248 non-null   object        
 9   Series_title_2    1182 non-null   object        
 10  Series_title_3    0 non-null      object        
 11  year              3248 non-null   int64         
 12  month             3248 non-null   int64         
 13  date              3248 non-null   datetime64[ns]
dtypes: datetime64[ns](1), float6

Graph shows nominal and real gross domestic product (GDP) in New Zealand from 1980 to 2025. Also shows percentage change in GDP for both meassures.

## Consumer Price Index (CPI)
Model seasonally adjusted (aggregate, tradeables vs non-tradeables).

In [98]:
# Load all the datasets in the existing
bop_quarterly_df = pd.read_csv('../../data/raw/nz_stats/economy/balance-of-payments-and-international-investment-position-march-2025-quarter.csv')
cpi_quarterly_df = pd.read_csv('../../data/raw/nz_stats/economy/consumers-price-index-june-2025-quarter-index-numbers.csv')
cpi_quarterly_sa_df = pd.read_csv('../../data/raw/nz_stats/economy/consumers-price-index-june-2025-quarter-seasonally-adjusted.csv')
cpi_quarterly_trade_df = pd.read_csv('../../data/raw/nz_stats/economy/consumers-price-index-june-2025-quarter-tradeables-and-non-tradeables.csv')
gdp_quarterly_df = pd.read_csv('../../data/raw/nz_stats/economy/gross-domestic-product-march-2025-quarter.csv')
hlci_df = pd.read_csv('../../data/raw/nz_stats/economy/household-living-costs-price-indexes-december-2024-quarter-time-series-indexes.csv')
na_quarterly_consolidated_df = pd.read_csv('../../data/raw/nz_stats/economy/na-isal-march-2025-quarter-consolidated-accounts.csv')
na_quarterly_institutional_df = pd.read_csv('../../data/raw/nz_stats/economy/na-isal-march-2025-quarter-institutional-sector-accounts.csv')
productivity_df = pd.read_csv('../../data/raw/nz_stats/economy/productivity-statistics-1978-2024.csv')
sel_ind_df = pd.read_csv('../../data/raw/nz_stats/economy/selected-price-indexes-july-2025.csv')

In [99]:
# Process and model seasonally adjusted CPI data
def process_cpi_sa(df: pd.DataFrame) -> pd.DataFrame:
    """
    Process CPI seasonally adjusted dataframe for analysis.
    :param raw df:
    :return: processed DataFrame
    """
    # Rename columns for clarity
    df = df.rename(columns={'Period': 'period', 'Data_value': 'value', 'STATUS': 'status'})
    # Convert period to timestamp e.g., 1980.03 to datetime
    df['year'] = df['period'].astype(str).str.split('.').str[0].astype(int)
    df['month'] = df['period'].astype(str).str.split('.').str[1].astype(int)
    date_df = df[['year', 'month']]
    df['date'] = pd.to_datetime(date_df.assign(day=1))
    return df

# Print unique values in the groups.
unique_groups = cpi_quarterly_sa_df['Group'].unique()

# Loop through the groups and print the unique values each group.
for group in unique_groups:
    group_df = cpi_quarterly_sa_df[cpi_quarterly_sa_df['Group'] == group]
    unique_series_1 = group_df['Series_title_1'].unique()
    unique_series_2 = group_df['Series_title_2'].unique()
    print(f"Group: {group}")
    print(f"Series 1: {unique_series_1}")
    print(f"Series 2: {unique_series_2}")
    print("\n")

Group: CPI Level 1 Groups for New Zealand, Seasonally adjusted
Series 1: ['Seasonally adjusted']
Series 2: ['Food' 'Alcoholic beverages and tobacco' 'Clothing and footwear'
 'Housing and household utilities' 'Household contents and services'
 'Health' 'Transport' 'Communication' 'Recreation and culture' 'Education'
 'Miscellaneous goods and services']


Group: CPI Level 2 Subgroups for New Zealand, Seasonally adjusted
Series 1: ['Seasonally adjusted']
Series 2: ['Fruit and vegetables' 'Meat, poultry and fish' 'Grocery food'
 'Non-alcoholic beverages' 'Restaurant meals and ready-to-eat food'
 'Alcoholic beverages' 'Cigarettes and tobacco' 'Clothing' 'Footwear'
 'Actual rentals for housing' 'Home ownership' 'Property maintenance'
 'Property rates and related services' 'Household energy'
 'Furniture, furnishings and floor coverings' 'Household textiles'
 'Household appliances' 'Glassware, tableware and household utensils'
 'Tools and equipment for house and garden'
 'Other household suppl

# Seasonally Adjusted CPI
Assess the impact of seasonally adjusted CPI data on aggregates.

1. 'CPI All Groups for New Zealand, Seasonally adjusted'
2. 'CPI Non-standard Tradable & Non-tradable series,Seasonally adjusted' - 'Tradable All Groups' vs 'Non-Tradable All Groups'

Note: Python enables to programmatically analyse different combinations of inflation data to place specific bets depending on the outcomes.

In [124]:
# Use the processing function to clean the CPI seasonally adjusted dataframe.
cpi_sa_processed_df = process_cpi_sa(cpi_quarterly_sa_df)
# Split the dataframe into three separate groups: All groups seasonally adjusted, Non-standard tradable and non-tradable, and tradable all groups.
cpi_sa_nz_df = cpi_sa_processed_df[cpi_sa_processed_df['Group'] == 'CPI All Groups for New Zealand, Seasonally adjusted']
cpi_sa_tradeable_df = cpi_sa_processed_df[cpi_sa_processed_df['Group'] == 'CPI Non-standard Tradable & Non-tradable series,Seasonally adjusted']
cpi_sa_tradeable_df = cpi_sa_tradeable_df[cpi_sa_tradeable_df['Series_title_2'] == 'Tradable All Groups']

cpi_sa_non_tradeable_df = cpi_sa_processed_df[cpi_sa_processed_df['Group'] == 'CPI Non-standard Tradable & Non-tradable series,Seasonally adjusted']
cpi_sa_non_tradeable_df = cpi_sa_non_tradeable_df[cpi_sa_non_tradeable_df['Series_title_2'] == 'Non-Tradable All Groups']

# Plot the three CPI seasonally adjusted groups.
# Create subplot with secondary y-axis
fig = make_subplots(specs=[[{"secondary_y": True}]])

# Left y-axis: CPI Index
fig.add_trace(
    go.Scatter(
        x=cpi_sa_nz_df["date"],
        y=cpi_sa_nz_df["value"],
        name="CPI All Groups (SA)",
        mode="lines",
        line=dict(color="blue")
    ),
    secondary_y=False
)

# Right y-axis: % Change (using pct_change * 100 like in your Matplotlib code)
fig.add_trace(
    go.Scatter(
        x=cpi_sa_nz_df["date"],
        y=cpi_sa_nz_df["value"].pct_change() * 100,
        name="CPI All Groups % Change (SA)",
        mode="lines",
        line=dict(color="orange", dash="dash")
    ),
    secondary_y=True
)

# Layout
fig.update_layout(
    title_text="New Zealand Consumer Price Index (CPI) - Seasonally Adjusted",
    height=600,
    width=1100,
    hovermode="x unified",
    legend=dict(orientation="h", yanchor="bottom", y=1.02, xanchor="left", x=0)
)

# Axis labels
fig.update_xaxes(title_text="Year", showgrid=True)
fig.update_yaxes(title_text="CPI Index", secondary_y=False, showgrid=True)
fig.update_yaxes(title_text="Percentage Change (%)", secondary_y=True)

fig.show()

# Create subplot with secondary y-axis
fig = make_subplots(specs=[[{"secondary_y": True}]])

# Left y-axis: CPI Index
fig.add_trace(
    go.Scatter(
        x=cpi_sa_tradeable_df["date"],
        y=cpi_sa_tradeable_df["value"],
        name="CPI Tradable All Groups (SA)",
        mode="lines",
        line=dict(color="blue")
    ),
    secondary_y=False
)

fig.add_trace(
    go.Scatter(
        x=cpi_sa_non_tradeable_df["date"],
        y=cpi_sa_non_tradeable_df["value"],
        name="CPI Non-Tradable All Groups (SA)",
        mode="lines",
        line=dict(color="orange")
    ),
    secondary_y=False
)

# Right y-axis: % Change
fig.add_trace(
    go.Scatter(
        x=cpi_sa_tradeable_df["date"],
        y=cpi_sa_tradeable_df["value"].pct_change() * 100,
        name="CPI Tradable % Change (SA)",
        mode="lines",
        line=dict(color="green", dash="dash")
    ),
    secondary_y=True
)

fig.add_trace(
    go.Scatter(
        x=cpi_sa_non_tradeable_df["date"],
        y=cpi_sa_non_tradeable_df["value"].pct_change() * 100,
        name="CPI Non-Tradable % Change (SA)",
        mode="lines",
        line=dict(color="red", dash="dash")
    ),
    secondary_y=True
)

# Layout
fig.update_layout(
    title_text="New Zealand Consumer Price Index (CPI) - Tradable vs Non-Tradable (Seasonally Adjusted)",
    height=600,
    width=1100,
    hovermode="x unified",
    legend=dict(orientation="h", yanchor="bottom", y=1.02, xanchor="left", x=0)
)

# Axis labels
fig.update_xaxes(title_text="Year", showgrid=True)
fig.update_yaxes(title_text="CPI Index", secondary_y=False, showgrid=True)
fig.update_yaxes(title_text="Percentage Change (%)", secondary_y=True)

fig.show()

  Series_reference   period  value   status  UNITS Subject  \
0      CPIQ.SE9S01  2006.06  762.0  REVISED  Index     CPI   
1      CPIQ.SE9S01  2006.09  771.0  REVISED  Index     CPI   
2      CPIQ.SE9S01  2006.12  780.0  REVISED  Index     CPI   
3      CPIQ.SE9S01  2007.03  788.0  REVISED  Index     CPI   
4      CPIQ.SE9S01  2007.06  794.0  REVISED  Index     CPI   

                                               Group       Series_title_1  \
0  CPI Level 1 Groups for New Zealand, Seasonally...  Seasonally adjusted   
1  CPI Level 1 Groups for New Zealand, Seasonally...  Seasonally adjusted   
2  CPI Level 1 Groups for New Zealand, Seasonally...  Seasonally adjusted   
3  CPI Level 1 Groups for New Zealand, Seasonally...  Seasonally adjusted   
4  CPI Level 1 Groups for New Zealand, Seasonally...  Seasonally adjusted   

  Series_title_2  year  month       date  
0           Food  2006      6 2006-06-01  
1           Food  2006      9 2006-09-01  
2           Food  2006     12 2006-

# Interest Rates
Models Federal reserve interest rates against currencies.
First, look at New Zealand's Key Trading Partners
Use Federal Reserve Economic Data (FRED) for US Data

In [101]:
# Define FRED Series IDs for key economic indicators.
gnpc = 'GNPCA' # Gross National Product
effr = 'EFFR' # Effective Federal Funds Rate
eftr = 'EFTR' # Effective Federal Funds Target Rate

# US Treasury Bond Yields
treasury_yields = {
    '1 Month': 'DGS1MO',
    '3 Month': 'DGS3MO',
    '6 Month': 'DGS6MO',
    '1 Year': 'DGS1',
    '2 Year': 'DGS2',
    '3 Year': 'DGS3',
    '5 Year': 'DGS5',
    '7 Year': 'DGS7',
    '10 Year': 'DGS10',
    '20 Year': 'DGS20',
    '30 Year': 'DGS30'
}

# Spot Exchange Rates (Daily)
# Real-time transaction systems will likely have the bid-ask spreads running.
spot_exchange_rates = {
    'USD/NZD' : 'DEXUSNZ', # US Dollar to New Zealand Dollar
    'USD/AUD' : 'DEXUSAL', # US Dollar to Australian Dollar
    'BRL/USD' : 'DEXBZUS', # Brazilian Real to US Dollar (BRL/USD)
    'CAD/USD' : 'DEXCAUS', # Canadian Dollar to US Dollar
    'CYN/USD' : 'DEXCHUS', # Chinese Yuan Renminbi to US Dollar
    'DKK/USD' : 'DEXDNUS', # Danish Krone to US Dollar
    'EUR/USD' : 'DEXUSEU', # Euro to US Dollar
    'HKD/USD' : 'DEXHKUS', # Hong Kong Dollar to US Dollar
    'INR/USD' : 'DEXINUS', # Indian Rupee to US Dollar
    'JPY/USD' : 'DEXJPUS', # Japanese Yen to US Dollar
    'MYR/USD' : 'DEXMAUS', # Malaysian Ringgit to US Dollar
    'MXN/USD' : 'DEXMXUS', # Mexican Peso to US Dollar
    'NOK/USD' : 'DEXNOUS', # Norwegian Krone to US Dollar
    'SGD/USD' : 'DEXSIUS', # Singapore Dollar to US Dollar
    'SAR/USD' : 'DEXSFUS', # South African Rand to US Dollar
    'KRW/USD' : 'DEXKOUS', # South Korean Won to US Dollar
    'LKR/USD' : 'DEXSLUS', # Sri Lankan Rupee to US Dollar
    'SEK/USD' : 'DEXSDUS', # Swedish Krona to US Dollar
    'CHF/USD' : 'DEXSZUS', # Swiss Franc to US Dollar
    'TWD/USD' : 'DEXTAUS', # Taiwan Dollar to US Dollar
    'USD/GBP' : 'DEXUSUK', # US Dollar to British Pound Sterling
    'VEF/USD' : 'DEXVZUS' # Venezuelan Bolivar to US Dollar
}

In [102]:
# Use requests library to fetch data from FRED API.
def fetch_fred_data(category: str, series_id: str, api_key: str, start_date: str = '2000-01-01', end_date: str = '2025-12-31'):
    """
    Fetch data from FRED API for a given series ID.
    :param category: Category of the economic indicator
    :param series_id: FRED series ID
    :param api_key: FRED API key
    :param start_date: Start date for data retrieval
    :param end_date: End date for data retrieval
    :return: DataFrame with date and value columns
    """
    url = f'https://api.stlouisfed.org/fred/series/observations?series_id={series_id}&api_key={api_key}&file_type=json&observation_start={start_date}&observation_end={end_date}'
    response = requests.get(url)
    data = response.json()
    # Save data to a JSON file for reference
    with open(f'../../data/raw/{category}/{series_id}.json', 'w') as f:
        import json
        json.dump(data, f, indent=4)
    f.close()
    return

# Initialize
dv.load_dotenv('../../.env')
fred_api_key = os.getenv('FRED_API_KEY')

# Loop through the spot exchange rates to fetch  their data
cat = 'exchange_rates'
for currency, series_id in spot_exchange_rates.items():
    try:
        fetch_fred_data(cat, series_id, fred_api_key)
    except Exception as e:
        print(f"Error fetching data for {series_id}: {e}")

In [103]:
# Use spot rates to calculate the cross rates against NZD.
# Retrieve codes for the relevant currencies from dictionary (trading partners).
currency_codes = list(spot_exchange_rates.keys())
print(currency_codes)
major_trading_partners = ['CYN/USD','USD/NZD','USD/AUD','JPY/USD','KRW/USD','SGD/USD'] # 50% Total Exports.

['USD/NZD', 'USD/AUD', 'BRL/USD', 'CAD/USD', 'CYN/USD', 'DKK/USD', 'EUR/USD', 'HKD/USD', 'INR/USD', 'JPY/USD', 'MYR/USD', 'MXN/USD', 'NOK/USD', 'SGD/USD', 'SAR/USD', 'KRW/USD', 'LKR/USD', 'SEK/USD', 'CHF/USD', 'TWD/USD', 'USD/GBP', 'VEF/USD']


In [104]:
# Retrieve observations from JSON & convert to dataframes.
def load_fred_json_to_df(category: str, series_id: str) -> pd.DataFrame:
    """
    Load FRED JSON data into a DataFrame.
    :param category: Category of the economic indicator
    :param series_id: FRED series ID
    :return: DataFrame with date and value columns
    """
    import json
    with open(f'../../data/raw/{category}/{series_id}.json', 'r') as f:
        data = json.load(f)
    f.close()
    observations = data.get('observations', [])
    df = pd.DataFrame(observations)
    df['date'] = pd.to_datetime(df['date'])
    df['value'] = pd.to_numeric(df['value'], errors='coerce')
    df = df[['date', 'value']]
    df['series_id'] = series_id
    df.to_csv(f'../../data/processed/{category}/{series_id}.csv', index=False)
    return df

In [105]:
# Loop through the spot exchange rates to load their data into dataframes.
exchange_rate_dfs = {}
cat = 'exchange_rates'
for partner in major_trading_partners:
    series_id = spot_exchange_rates[partner]
    try:
        df = load_fred_json_to_df(cat, series_id)
        df.rename(columns={'value': f'{partner.replace("/", "_")}'}, inplace=True)
        df.drop(columns=['series_id'], inplace=True)
        print(df.head())
        exchange_rate_dfs[partner] = df
        print(f"Loaded data for {series_id}: {df.shape[0]} records")
    except Exception as e:
        print(f"Error loading data for {series_id}: {e}")


        date  CYN_USD
0 2000-01-03   8.2798
1 2000-01-04   8.2799
2 2000-01-05   8.2798
3 2000-01-06   8.2797
4 2000-01-07   8.2794
Loaded data for DEXCHUS: 6700 records
        date  USD_NZD
0 2000-01-03   0.5254
1 2000-01-04   0.5198
2 2000-01-05   0.5171
3 2000-01-06   0.5145
4 2000-01-07   0.5160
Loaded data for DEXUSNZ: 6700 records
        date  USD_AUD
0 2000-01-03   0.6591
1 2000-01-04   0.6562
2 2000-01-05   0.6550
3 2000-01-06   0.6540
4 2000-01-07   0.6548
Loaded data for DEXUSAL: 6700 records
        date  JPY_USD
0 2000-01-03   101.70
1 2000-01-04   103.09
2 2000-01-05   103.77
3 2000-01-06   105.19
4 2000-01-07   105.17
Loaded data for DEXJPUS: 6700 records
        date  KRW_USD
0 2000-01-03   1128.0
1 2000-01-04   1122.5
2 2000-01-05   1135.0
3 2000-01-06   1146.5
4 2000-01-07   1138.0
Loaded data for DEXKOUS: 6700 records
        date  SGD_USD
0 2000-01-03   1.6563
1 2000-01-04   1.6535
2 2000-01-05   1.6560
3 2000-01-06   1.6655
4 2000-01-07   1.6625
Loaded data for DE

In [106]:
# Merge all the dataframes on the date column.
merged_exchange_rates_df = None
for df in exchange_rate_dfs.values():
    if merged_exchange_rates_df is None:
        merged_exchange_rates_df = df
    else:
        merged_exchange_rates_df = pd.merge(merged_exchange_rates_df, df, on='date', how='outer')
# Sort by date
merged_exchange_rates_df = merged_exchange_rates_df.sort_values(by='date').reset_index(drop=True)
print(merged_exchange_rates_df.head())

        date  CYN_USD  USD_NZD  USD_AUD  JPY_USD  KRW_USD  SGD_USD
0 2000-01-03   8.2798   0.5254   0.6591   101.70   1128.0   1.6563
1 2000-01-04   8.2799   0.5198   0.6562   103.09   1122.5   1.6535
2 2000-01-05   8.2798   0.5171   0.6550   103.77   1135.0   1.6560
3 2000-01-06   8.2797   0.5145   0.6540   105.19   1146.5   1.6655
4 2000-01-07   8.2794   0.5160   0.6548   105.17   1138.0   1.6625


In [107]:
# Calculate the cross rates against NZD
merged_exchange_rates_df['CYN_NZD'] = merged_exchange_rates_df['CYN_USD'] * merged_exchange_rates_df['USD_NZD']
merged_exchange_rates_df['AUD_NZD'] = merged_exchange_rates_df['USD_NZD'] / merged_exchange_rates_df['USD_AUD']
merged_exchange_rates_df['JPY_NZD'] = merged_exchange_rates_df['JPY_USD'] * merged_exchange_rates_df['USD_NZD']
merged_exchange_rates_df['KRW_NZD'] = merged_exchange_rates_df['KRW_USD'] * merged_exchange_rates_df['USD_NZD']
merged_exchange_rates_df['SGD_NZD'] = merged_exchange_rates_df['SGD_USD'] * merged_exchange_rates_df['USD_NZD']
print(merged_exchange_rates_df.tail())

           date  CYN_USD  USD_NZD  USD_AUD  JPY_USD  KRW_USD  SGD_USD  \
6695 2025-09-01      NaN      NaN      NaN      NaN      NaN      NaN   
6696 2025-09-02   7.1390   0.5864   0.6516   148.23  1394.76   1.2880   
6697 2025-09-03   7.1415   0.5881   0.6550   147.97  1389.21   1.2873   
6698 2025-09-04   7.1414   0.5838   0.6514   148.63  1394.80   1.2894   
6699 2025-09-05   7.1323   0.5910   0.6570   146.84  1385.28   1.2827   

       CYN_NZD   AUD_NZD    JPY_NZD     KRW_NZD   SGD_NZD  
6695       NaN       NaN        NaN         NaN       NaN  
6696  4.186310  0.899939  86.922072  817.887264  0.755283  
6697  4.199916  0.897863  87.021157  816.994401  0.757061  
6698  4.169149  0.896224  86.770194  814.284240  0.752752  
6699  4.215189  0.899543  86.782440  818.700480  0.758076  


In [108]:
# Calculate percentage changes for each of the cross rates with NZD.
for col in ['CYN_NZD', 'AUD_NZD', 'JPY_NZD', 'KRW_NZD', 'SGD_NZD']:
    merged_exchange_rates_df[f'{col}_pct_change'] = merged_exchange_rates_df[col].pct_change() * 100
# Save the merged dataframe to CSV
merged_exchange_rates_df.to_csv('../../data/processed/exchange_rates/major_trading_partners_cross_rates.csv', index=False)


/var/folders/t8/tgk2l0r11nz2x710wd9bn3_w0000gq/T/ipykernel_43934/4200088544.py:3: FutureWarning:

The default fill_method='pad' in Series.pct_change is deprecated and will be removed in a future version. Either fill in any non-leading NA values prior to calling pct_change or specify 'fill_method=None' to not fill NA values.

/var/folders/t8/tgk2l0r11nz2x710wd9bn3_w0000gq/T/ipykernel_43934/4200088544.py:3: FutureWarning:

The default fill_method='pad' in Series.pct_change is deprecated and will be removed in a future version. Either fill in any non-leading NA values prior to calling pct_change or specify 'fill_method=None' to not fill NA values.

/var/folders/t8/tgk2l0r11nz2x710wd9bn3_w0000gq/T/ipykernel_43934/4200088544.py:3: FutureWarning:

The default fill_method='pad' in Series.pct_change is deprecated and will be removed in a future version. Either fill in any non-leading NA values prior to calling pct_change or specify 'fill_method=None' to not fill NA values.

/var/folders/t8/tgk

In [109]:
# Plot the cross rates against NZD
cross_rate_cols = ['CYN_NZD', 'AUD_NZD', 'JPY_NZD', 'KRW_NZD', 'SGD_NZD']

# Create subplot grid (3 rows x 2 columns so it fits 5 plots)
fig = make_subplots(rows=3, cols=2, subplot_titles=cross_rate_cols)

# Add each currency as its own subplot
for i, col in enumerate(cross_rate_cols):
    row = i // 2 + 1
    col_idx = i % 2 + 1
    fig.add_trace(
        go.Scatter(x=merged_exchange_rates_df["date"], y=merged_exchange_rates_df[col], name=col),
        row=row, col=col_idx
    )

# Update layout
fig.update_layout(
    height=900, width=1200,
    title_text="Exchange Rates vs NZD",
    showlegend=False
)

# Show interactive figure
fig.show()

In [110]:
# Plot percentage changes for each of the cross rates on a figure with 6 subplots.
# Create subplot grid (3 rows x 2 columns so it fits 5 plots)
fig = make_subplots(rows=3, cols=2, subplot_titles=cross_rate_cols)

# Add each currency as its own subplot
for i, col in enumerate(cross_rate_cols):
    row = i // 2 + 1
    col_idx = i % 2 + 1
    x = f'{col}_pct_change'
    fig.add_trace(
        go.Scatter(x=merged_exchange_rates_df["date"], y=merged_exchange_rates_df[x], name=col),
        row=row, col=col_idx
    )
    # Add axis labels for each subplot
    fig.update_xaxes(title_text="Date", row=row, col=col_idx)
    fig.update_yaxes(title_text="% Change", row=row, col=col_idx)

# Update layout
fig.update_layout(
    height=900, width=1200,
    title_text="Exchange Rates vs NZD",
    showlegend=False
)

# Show interactive figure
fig.show()

In [111]:
# Reproduce % changes but for only last 30 days to better show changes
recent_exchange_rates_df = merged_exchange_rates_df[merged_exchange_rates_df['date'] >= (merged_exchange_rates_df['date'].max() - pd.Timedelta(days=14))]
# Create subplot grid (3 rows x 2 columns so it fits 5 plots)
fig = make_subplots(rows=3, cols=2, subplot_titles=cross_rate_cols)

# Add each currency as its own subplot
for i, col in enumerate(cross_rate_cols):
    row = i // 2 + 1
    col_idx = i % 2 + 1
    x = f'{col}_pct_change'
    fig.add_trace(
        go.Scatter(x=recent_exchange_rates_df["date"], y=recent_exchange_rates_df[x], name=col),
        row=row, col=col_idx
    )
    # Add axis labels for each subplot
    fig.update_xaxes(title_text="Date", row=row, col=col_idx)
    fig.update_yaxes(title_text="Change (bps)", row=row, col=col_idx)

# Update layout
fig.update_layout(
    height=900, width=1200,
    title_text="Exchange Rates vs NZD",
    showlegend=False
)

# Show interactive figure
fig.show()

# Trade Balances evaluate trade balances across
GDI Index: Diary

In [112]:
# Visualise trading balances across
# Import relevant trade balances.
trade_output_df = pd.read_csv('../../data/raw/nz_stats/business/international-trade-march-2025-quarter/output_csv_full.csv')
country_codes_df = pd.read_csv('../../data/raw/nz_stats/business/international-trade-march-2025-quarter/country_classification.csv')
goods_lvl_2_df = pd.read_csv('../../data/raw/nz_stats/business/international-trade-march-2025-quarter/goods_classification.csv')
goods_lvl_1_df = pd.read_csv('../../data/raw/nz_stats/business/international-trade-march-2025-quarter/goods_classification.csv')
services_df = pd.read_csv('../../data/raw/nz_stats/business/international-trade-march-2025-quarter/services_classification.csv')


In [113]:
# Rename relevant code columns for merging and delete other column.
goods_lvl_1_df = goods_lvl_1_df.rename(columns={'NZHSC_Level_1_Code_HS2':'code'})
goods_lvl_1_df = goods_lvl_1_df.drop(columns=['NZHSC_Level_2_Code_HS4'])
goods_lvl_2_df = goods_lvl_2_df.rename(columns={'NZHSC_Level_2_Code_HS4':'code'})
goods_lvl_2_df = goods_lvl_2_df.rename(columns={'NZHSC_Level_1_Code_HS2':'group'})

# Convert the timeref column (202503) to a datetime format.
trade_output_df['year'] = trade_output_df['time_ref'].astype(str).str[:4].astype(int)
trade_output_df['month'] = trade_output_df['time_ref'].astype(str).str[4:6].astype(int)
date_df = trade_output_df[['year', 'month']]
trade_output_df['date'] = pd.to_datetime(date_df.assign(day=1))

# Join the classifications to the main output dataframe
trade_goods_df = trade_output_df[trade_output_df['product_type'] == 'Goods']
trade_services_df = trade_output_df[trade_output_df['product_type'] == 'Services']

# Create a dataframe which is just goods and services.
total_goods_df = trade_goods_df[trade_goods_df['code'] == '00']
total_goods_df = total_goods_df.merge(country_codes_df, on='country_code', how='left')
total_goods_df.to_csv('../../data/processed/nz_stats/trade/total_trade_goods.csv')

# Covert the goods codes to numeric for easier filtering.
trade_goods_df.loc[:, 'code'] = pd.to_numeric(trade_goods_df['code'], errors='coerce')
trade_goods_lvl_1 = trade_goods_df[trade_goods_df['code'] < 100]
trade_goods_lvl_2 = trade_goods_df[trade_goods_df['code'] >=100]

# Merge the country codes, goods and services classifications to the main trade output dataframe.
# Goods Level 1
goods_lvl_1_total = trade_goods_lvl_1.merge(country_codes_df, on='country_code', how='left')
goods_lvl_1_total = goods_lvl_1_total.merge(goods_lvl_1_df, on='code', how='left')
goods_lvl_1_total.to_csv('../../data/processed/nz_stats/trade/trade_goods_lvl_1.csv')
# Goods Level 2
goods_lvl_2_total = trade_goods_lvl_2.merge(country_codes_df, on='country_code', how='left')
goods_lvl_2_total = goods_lvl_2_total.merge(goods_lvl_2_df, on='code', how='left')
goods_lvl_2_total.to_csv('../../data/processed/nz_stats/trade/trade_goods_lvl_2.csv')
# Services
services_total = trade_services_df.merge(country_codes_df, on='country_code', how='left')
services_total = services_total.merge(services_df, on='code', how='left')
services_total.to_csv('../../data/processed/nz_stats/trade/trade_services.csv')


In [114]:
# Visualise the trade balances for each of New Zealand's Major Trading Partners (China, Australia, USA, Japan, UK, Eurozone, South Korea)
processed_goods_lvl_1_df = pd.read_csv('../../data/processed/nz_stats/trade/trade_goods_lvl_1.csv')
processed_goods_lvl_2_df = pd.read_csv('../../data/processed/nz_stats/trade/trade_goods_lvl_2.csv')
processed_services_df = pd.read_csv('../../data/processed/nz_stats/trade/trade_services.csv')
processed_total_goods_df = pd.read_csv('../../data/processed/nz_stats/trade/total_trade_goods.csv')


In [115]:
# Create a tree maps for
quarter = '202503' # YYYYMM
processed_total_goods_df = processed_total_goods_df[processed_total_goods_df['time_ref'] == int(quarter)]
processed_total_goods_df.to_csv('../../data/processed/nz_stats/trade/total_trade_qtr.csv')
total_exports = processed_total_goods_df[processed_total_goods_df['account'] == 'Exports']
total_imports = processed_total_goods_df[processed_total_goods_df['account'] == 'Imports']

# Print the sum of total exports and imports to verify data integrity.
print(f"Total Exports: {total_exports['value'].sum()}")
print(f"Total Imports: {total_imports['value'].sum()}")

# Crate a tree map here.
try:
    fig_tot_exp = px.treemap(
        total_exports,
        path=['country_label'],
        values='value',
        title='Total Aotearoa Exports ($, Goods) by Country'
    )
    # Update the trace to display the values inside the blocks
    fig_tot_exp.update_traces(
        textinfo="label+value+percent parent"
    )
    fig_tot_exp.show()
except ValueError as ve:
    print(f"ValueError: {ve}")
    print("Check if the 'value' column contains non-numeric data.")
    print(total_exports['value'].head())

Total Exports: 20080810665.0
Total Imports: 18499832174.0


In [116]:
# Create tree maps from major trading partners.
# Crate a tree map here.
try:
    fig_tot_imp = px.treemap(
        total_imports,
        path=['country_label'],
        values='value',
        title='Total Aotearoa New Zealand Imports ($, Goods) by Country'
    )
    # Update the trace to display the values inside the blocks
    fig_tot_imp.update_traces(
        textinfo="label+value+percent parent"
    )
    fig_tot_imp.show()
except ValueError as ve:
    print(f"ValueError: {ve}")
    print("Check if the 'value' column contains non-numeric data.")
    print(total_imports['value'].head())

In [117]:
# Create a tree maps
major_trading_partners = ['CN','US','AU','JP','KP','SG'] # 50% Total Exports.
trade_partners_df = processed_goods_lvl_2_df[processed_goods_lvl_2_df['country_code'].isin(major_trading_partners)] # Filter for major trading partners.
trade_partners_df = trade_partners_df[trade_partners_df['time_ref'] == int(quarter)] # Filter for the latest quarter.
trade_partners_df.to_csv('../../data/processed/nz_stats/trade/trade_partners_qtr.csv') # Save the filtered dataframe.
trade_partners_exports = trade_partners_df[trade_partners_df['account'] == 'Exports'] # Filter for specific imports.
trade_partners_imports = trade_partners_df[trade_partners_df['account'] == 'Imports'] # Filter for specific imports.

In [118]:
# Create a tree map for major trading partner and their exports.
try:
    fig_tot_exp_lvl_1 = px.treemap(
        trade_partners_exports,
        path=['country_label', 'NZHSC_Level_1'],
        values='value',
        title='Total Aotearoa New Zealand Exports ($, Goods, NZHSC Level 1) to Top Trading Partners (China, USA, Australia, Japan, South Korea, Singapore)'
    )
    # Update the trace to display the values inside the blocks
    fig_tot_exp_lvl_1.update_traces(
        textinfo="label+value+percent parent"
    )
    fig_tot_exp_lvl_1.show()
except ValueError as ve:
    print(f"ValueError: {ve}")
    print("Check if the 'value' column contains non-numeric data.")
    print(total_exports['value'].head())

try:
    fig_tot_exp_lvl_2 = px.treemap(
        trade_partners_exports,
        path=['country_label', 'NZHSC_Level_2'],
        values='value',
        title='Total Aotearoa New Zealand Exports ($, Goods, NZHSC Level 2) to Top Trading Partners (China, USA, Australia, Japan, South Korea, Singapore)'
    )
    # Update the trace to display the values inside the blocks
    fig_tot_exp_lvl_2.update_traces(
        textinfo="label+value+percent parent"
    )
    fig_tot_exp_lvl_2.show()
except ValueError as ve:
    print(f"ValueError: {ve}")
    print("Check if the 'value' column contains non-numeric data.")
    print(total_exports['value'].head())

In [119]:
# Create Tree Maps for Import Data
# Create a tree maps for major trading partner and their exports.
# Crate a tree map here.
try:
    fig_tot_imp_lvl_1 = px.treemap(
        trade_partners_imports,
        path=['country_label', 'NZHSC_Level_1'],
        values='value',
        title='Total Aotearoa New Zealand Imports ($, Goods, NZHSC Level 1) from Top Trading Partners (China, USA, Australia, Japan, South Korea, Singapore)'
    )
    # Update the trace to display the values inside the blocks
    fig_tot_imp_lvl_1.update_traces(
        textinfo="label+value+percent parent"
    )
    fig_tot_imp_lvl_1.show()
except ValueError as ve:
    print(f"ValueError: {ve}")
    print("Check if the 'value' column contains non-numeric data.")
    print(total_exports['value'].head())

try:
    fig_tot_imp_lvl_2 = px.treemap(
        trade_partners_imports,
        path=['country_label', 'NZHSC_Level_2'],
        values='value',
        title='Total Aotearoa New Zealand Imports ($, Goods, NZHSC Level 2) from Top Trading Partners (China, USA, Australia, Japan, South Korea, Singapore)'
    )
    # Update the trace to display the values inside the blocks
    fig_tot_imp_lvl_2.update_traces(
        textinfo="label+value+percent parent"
    )
    fig_tot_imp_lvl_2.show()
except ValueError as ve:
    print(f"ValueError: {ve}")
    print("Check if the 'value' column contains non-numeric data.")
    print(total_exports['value'].head())

In [120]:
# Complete the set by looking at services.
# Split the services dataframe into exports and imports.
# Create a tree maps for
quarter = '202503' # YYYYMM
processed_services_df = pd.read_csv('../../data/processed/nz_stats/trade/trade_services.csv')
processed_services_qtr_df = processed_services_df[processed_services_df['time_ref'] == int(quarter)]
processed_services_qtr_df.to_csv('../../data/processed/nz_stats/trade/total_services_qtr.csv')

# Split into aggregates and granular reporting.
aggregate_services = processed_services_qtr_df[(processed_services_qtr_df['code'] == 'A12')]
aggregate_services = aggregate_services[aggregate_services['country_label'] != 'Total']
granulated_services = processed_services_qtr_df[(processed_services_qtr_df['code'] != 'A12')]
granulated_services = granulated_services[granulated_services['country_label'] != 'Total']

# Save the dataframes.
aggregate_services.to_csv('../../data/processed/nz_stats/trade/aggregate_services_qtr.csv')
granulated_services.to_csv('../../data/processed/nz_stats/trade/granulated_services_qtr.csv')

# Split into the exports and imports.
aggregated_services_exports = aggregate_services[aggregate_services['account'] == 'Exports']
aggregated_services_imports = aggregate_services[aggregate_services['account'] == 'Imports']
granular_services_exports = granulated_services[granulated_services['account'] == 'Exports']
granular_services_imports = granulated_services[granulated_services['account'] == 'Imports']

# Create a services tree map for exports and imports.
# Exports
try:
    fig_tot_exp_ser = px.treemap(
        aggregated_services_exports,
        path=['country_label'],
        values='value',
        title='Total Aotearoa exports ($, Services) by Country'
    )
    # Update the trace to display the values inside the blocks
    fig_tot_exp_ser.update_traces(
        textinfo="label+value+percent parent"
    )
    fig_tot_exp_ser.show()
except ValueError as ve:
    print(f"ValueError: {ve}")
    print("Check if the 'value' column contains non-numeric data.")
    print(total_exports['value'].head())
# Imports
try:
    fig_tot_imp_ser = px.treemap(
        aggregated_services_imports,
        path=['country_label'],
        values='value',
        title='Total Aotearoa imports ($, Services) by Country'
    )
    # Update the trace to display the values inside the blocks
    fig_tot_imp_ser.update_traces(
        textinfo="label+value+percent parent"
    )
    fig_tot_imp_ser.show()
except ValueError as ve:
    print(f"ValueError: {ve}")
    print("Check if the 'value' column contains non-numeric data.")
    print(total_exports['value'].head())

In [121]:
# Model granulated services data for exports and imports using major trading partners.
major_trading_partners = ['CN','US','AU','JP','KP','SG','GB']
granular_services_exports = granular_services_exports[granular_services_exports['country_code'].isin(major_trading_partners)] # Filter for major trading partners.
granular_services_imports = granular_services_imports[granular_services_imports['country_code'].isin(major_trading_partners)] # Filter for major trading partners.
# Exports
try:
    fig_gra_exp_ser = px.treemap(
        granular_services_exports,
        path=['country_label','service_label'],
        values='value',
        title='Total Aotearoa New Zealand exports ($, Services) by Major Trading Partner & Services'
    )
    # Update the trace to display the values inside the blocks
    fig_gra_exp_ser.update_traces(
        textinfo="label+value+percent parent"
    )
    fig_gra_exp_ser.show()
except ValueError as ve:
    print(f"ValueError: {ve}")
    print("Check if the 'value' column contains non-numeric data.")
    print(total_exports['value'].head())
# Imports
try:
    fig_gra_imp_ser = px.treemap(
        granular_services_imports,
        path=['country_label','service_label'],
        values='value',
        title='Total Aotearoa New Zealand imports ($, Services) by Country'
    )
    # Update the trace to display the values inside the blocks
    fig_gra_imp_ser.update_traces(
        textinfo="label+value+percent parent"
    )
    fig_gra_imp_ser.show()
except ValueError as ve:
    print(f"ValueError: {ve}")
    print("Check if the 'value' column contains non-numeric data.")
    print(total_exports['value'].head())

# Equity Market Performance
Compare equity market performance between trading partners:
- Rebased levels: all indices starting at 100 on the first common month
- Monthly returns heatmap: rows = indices, columns = months, values in %.
- Rolling 12-month correlation: each index’s correlation to the S&P 500.
- Drawdowns: depth below the running peak (in %).

In [125]:
# --- Tickers (Yahoo Finance) ---
tickers = {
    "NZX 50 (NZ)": "^NZ50",        # S&P/NZX 50 Gross Index
    "S&P 500 (US)": "^GSPC",
    "ASX 200 (AU)": "^AXJO",
    "CSI 300 (CN)": "000300.SS",   # or "000001.SS" for SSE Composite
    "STI (SG)": "^STI",
    "FTSE 100 (UK)": "^FTSE",
    "KOSPI (KR)": "^KS11"          # or "^KS200" for KOSPI 200
}

# --- Download price history ---
# Choose your window; monthly is often cleaner for cross-market comparisons
start = "2005-01-01"  # adjust as needed
data = yf.download(list(tickers.values()), start=start, interval="1d", auto_adjust=True, progress=False)

# Keep only the closing prices (Adj Close already auto_adjusted=True)
prices = data["Close"].copy()

# Rename columns from tickers to friendly names
rename_map = {v: k for k, v in tickers.items()}
prices = prices.rename(columns=rename_map)

# Optional: convert to month-end to smooth noise and align calendars
monthly = prices.resample("M").last().dropna(how="all")

# --- Rebase to 100 at the first available common date ---
# Align on the first date where all markets have data to avoid spurious jumps
aligned = monthly.dropna(axis=0, how="any")
rebased = aligned / aligned.iloc[0] * 100

# --- Compute monthly % returns (for correlation/analytics if needed) ---
returns = aligned.pct_change().dropna()

# --- Plot: Rebased indices (interactive) ---
melted = rebased.reset_index().melt(id_vars="Date", var_name="Index", value_name="Rebased (=100)")
fig = px.line(
    melted, x="Date", y="Rebased (=100)", color="Index",
    title="Global Equity Benchmarks (Rebased to 100)",
    labels={"Date": "Date", "Rebased (=100)": "Index Level (Rebased)"}
)
fig.update_layout(height=600, width=1100, hovermode="x unified")
fig.show()

/var/folders/t8/tgk2l0r11nz2x710wd9bn3_w0000gq/T/ipykernel_43934/2259257587.py:25: FutureWarning:

'M' is deprecated and will be removed in a future version, please use 'ME' instead.



In [126]:
# -----------------------------
# 1) Download and prep the data
# -----------------------------
tickers = {
    "NZX 50 (NZ)": "^NZ50",        # S&P/NZX 50 Gross Index
    "S&P 500 (US)": "^GSPC",
    "ASX 200 (AU)": "^AXJO",
    "CSI 300 (CN)": "000300.SS",   # alt: "000001.SS" (SSE Composite)
    "STI (SG)": "^STI",
    "FTSE 100 (UK)": "^FTSE",
    "KOSPI (KR)": "^KS11"          # alt: "^KS200" (KOSPI 200)
}

start = "2005-01-01"

raw = yf.download(
    list(tickers.values()),
    start=start,
    interval="1d",
    auto_adjust=True,
    progress=False
)

# Use Close, rename to friendly names
prices = raw["Close"].rename(columns={v: k for k, v in tickers.items()})

# Move to month-end to align calendars and reduce noise
monthly = prices.resample("M").last()

# Align on common dates (drop rows with any missing)
aligned = monthly.dropna(how="any")

# Rebase to 100 at the first common date
rebased = aligned / aligned.iloc[0] * 100

# Monthly returns (decimal)
rets = aligned.pct_change().dropna()

# Drawdowns: (P / cummax) - 1
cummax = aligned.cummax()
drawdowns = aligned / cummax - 1.0

# Rolling 12-month correlation vs S&P 500 (use returns)
base_name = "S&P 500 (US)"
rolling_corr = (
    rets.rolling(12)
        .corr(rets[base_name])
        .drop(columns=[base_name], errors="ignore")
)

# -----------------------------
# 2) Build the 2×2 dashboard
# -----------------------------
titles = [
    "Rebased Levels (=100 at first common date)",
    "Monthly Returns Heatmap",
    "Rolling 12-Month Correlation vs S&P 500",
    "Drawdowns"
]

fig = make_subplots(
    rows=2, cols=2,
    subplot_titles=titles,
    specs=[[{"type": "xy"}, {"type": "heatmap"}],
           [{"type": "xy"}, {"type": "xy"}]],
    vertical_spacing=0.12,
    horizontal_spacing=0.08
)

# ---- (1) Rebased levels (row 1, col 1)
for col in rebased.columns:
    fig.add_trace(
        go.Scatter(
            x=rebased.index, y=rebased[col],
            mode="lines", name=col, legendgroup="levels", showlegend=True
        ),
        row=1, col=1
    )
fig.update_xaxes(title_text="Date", row=1, col=1)
fig.update_yaxes(title_text="Index Level (Rebased)", row=1, col=1)

# ---- (2) Monthly returns heatmap (row 1, col 2)
# Heatmap expects 2D array (rows = indices, cols = dates)
heat_data = (rets * 100).T  # % terms
fig.add_trace(
    go.Heatmap(
        z=heat_data.values,
        x=heat_data.columns,
        y=heat_data.index,
        coloraxis="coloraxis",
        hovertemplate="Date=%{x|%Y-%m}<br>%{y}: %{z:.2f}%<extra></extra>"
    ),
    row=1, col=2
)
fig.update_xaxes(title_text="Date", row=1, col=2)
fig.update_yaxes(title_text="Index", row=1, col=2)

# ---- (3) Rolling 12m corr vs S&P 500 (row 2, col 1)
for col in rolling_corr.columns:
    fig.add_trace(
        go.Scatter(
            x=rolling_corr.index, y=rolling_corr[col],
            mode="lines", name=f"{col} vs {base_name}",
            legendgroup="corr", showlegend=True
        ),
        row=2, col=1
    )
fig.update_xaxes(title_text="Date", row=2, col=1)
fig.update_yaxes(title_text="Correlation (12m)", range=[-1, 1], row=2, col=1)

# ---- (4) Drawdowns (row 2, col 2)
for col in drawdowns.columns:
    fig.add_trace(
        go.Scatter(
            x=drawdowns.index, y=drawdowns[col],
            mode="lines", name=f"{col} Drawdown",
            legendgroup="dd", showlegend=True
        ),
        row=2, col=2
    )
fig.update_xaxes(title_text="Date", row=2, col=2)
fig.update_yaxes(title_text="Drawdown", tickformat=".0%", row=2, col=2)

# -----------------------------
# 3) Layout / Styling
# -----------------------------
fig.update_layout(
    title_text="Global Equity Benchmarks Dashboard",
    height=900, width=1300,
    hovermode="x unified",
    legend=dict(orientation="h", yanchor="bottom", y=1.06, xanchor="left", x=0),
    coloraxis=dict(
        colorscale="RdBu",
        cmin=-8, cmax=8,  # clamp heatmap around ±8% monthly; adjust to taste
        colorbar=dict(title="% Monthly Return")
    ),
    margin=dict(l=60, r=40, t=90, b=60)
)

# Make correlations and drawdowns show sensible hover
fig.update_traces(hovertemplate=None, selector=dict(type="scatter"))

fig.show()

/var/folders/t8/tgk2l0r11nz2x710wd9bn3_w0000gq/T/ipykernel_43934/361927105.py:28: FutureWarning:

'M' is deprecated and will be removed in a future version, please use 'ME' instead.



# Commodity Price
Model performance of proxies to commodity prices to help with relative performance.

In [128]:
# --- 1) Commodity proxies (Yahoo Finance tickers) ---
commodities = {
    "Class III Milk": "DC=F",
    "Butter": "CB=F",
    "Lumber": "LBS=F",
    "Global Timber ETF": "WOOD",   # equity proxy for forestry
    "Live Cattle": "LE=F",
    "Feeder Cattle": "GF=F",
    "Lean Hogs": "HE=F",           # broad protein proxy
    "Corn": "ZC=F",                # feed input
    "Soybean Meal": "ZM=F",        # feed input
    "Crude Oil": "CL=F"            # transport/energy input
}

start = "2005-01-01"

# --- 2) Download daily closes ---
raw = yf.download(list(commodities.values()), start=start, interval="1d",
                  auto_adjust=True, progress=False)

# Keep Close prices; rename to friendly names
prices = raw["Close"].rename(columns={v: k for k, v in commodities.items()})

# --- 3) Resample to month-end and align ---
monthly = prices.resample("M").last()
aligned = monthly.dropna(how="any")  # keep only common dates

# --- 4) Rebase to 100 at first common date ---
rebased = aligned / aligned.iloc[0] * 100

# --- 5) Monthly returns (%)
returns = aligned.pct_change().dropna() * 100  # percent

# --- 6) Create dashboard (2×1: line + heatmap) ---
fig = make_subplots(
    rows=2, cols=1,
    subplot_titles=(
        "Commodities Rebased to 100 (First Common Date)",
        "Monthly Returns Heatmap (%)"
    ),
    row_heights=[0.65, 0.35],
    vertical_spacing=0.12,
    specs=[[{"type": "xy"}], [{"type": "heatmap"}]]
)

# --- Line plot (rebased) ---
for col in rebased.columns:
    fig.add_trace(
        go.Scatter(x=rebased.index, y=rebased[col], mode="lines", name=col),
        row=1, col=1
    )
fig.update_xaxes(title_text="Date", row=1, col=1)
fig.update_yaxes(title_text="Rebased Index (=100)", row=1, col=1)

# --- Heatmap of monthly returns ---
heat_data = returns.T  # rows = commodities, cols = dates
fig.add_trace(
    go.Heatmap(
        z=heat_data.values,
        x=heat_data.columns,
        y=heat_data.index,
        colorscale="RdBu",
        zmid=0,
        colorbar=dict(title="% Monthly Return"),
        hovertemplate="Date=%{x|%Y-%m}<br>%{y}: %{z:.2f}%<extra></extra>"
    ),
    row=2, col=1
)
fig.update_xaxes(title_text="Date", row=2, col=1)
fig.update_yaxes(title_text="Commodity", row=2, col=1)

# --- Layout ---
fig.update_layout(
    title_text="NZ Export-Linked Commodities Dashboard",
    height=900, width=1200,
    hovermode="x unified",
    legend=dict(orientation="h", yanchor="bottom", y=1.02, xanchor="left", x=0)
)

fig.show()

/var/folders/t8/tgk2l0r11nz2x710wd9bn3_w0000gq/T/ipykernel_43934/4011971090.py:25: FutureWarning:

'M' is deprecated and will be removed in a future version, please use 'ME' instead.

